<b><c>Capstone Project -The Battle of Neighborhoods</c></b>
In this project we will use location data to explore a geographical location to find good place to open a restaurant in New york

Problem
In this project : Where is the proper location to open a restaurant in New york?

Data is being collected from wikipedia and Foursquare

List of neighborhoods in New york from NYU Spatial data (https://geo.nyu.edu/catalog/nyu_2451_34572)
Foursquare

In [5]:
#loading libraries
import numpy as np
import pandas as pd
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

from geopy.geocoders import Nominatim
import urllib.request
import json
from bs4 import BeautifulSoup
from urllib.request import urlopen
import requests
from pandas.io.json import json_normalize

import matplotlib.cm as cm
import matplotlib.colors as colors

import matplotlib.cm as cm
import matplotlib.pyplot as plt
import matplotlib.colors as colors
%matplotlib inline
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes
import folium

print('Libraries imported.')


Libraries imported.


In [6]:
#downloading the dataset
from urllib.request import urlopen
import requests
from pandas.io.json import json_normalize
!wget -q -O 'newyork_data.json' https://cocl.us/new_york_dataset
print('Data downloaded!')

with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)

Data downloaded!


In [181]:
# dataframe
neighborhoods_data = newyork_data['features']
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 
neighborhoods = pd.DataFrame(columns=column_names)

for data in neighborhoods_data:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    neighborhoods = neighborhoods.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)


In [182]:
neighborhoods.head()

Borough Neighborhood   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201
1   Bronx   Co-op City  40.874294 -73.829939
2   Bronx  Eastchester  40.887556 -73.827806
3   Bronx    Fieldston  40.895437 -73.905643
4   Bronx    Riverdale  40.890834 -73.912585

In [183]:
#getting latitude and longitude of newyork
address = 'New York City, NY'

geolocator = Nominatim(user_agent="ny_agent")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of New York City are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of New York City are 40.7127281, -74.0060152.


In [184]:
neighborhoods.shape

(306, 4)

In [185]:
latitude = 40.7127281
longitude = -74.0060152

map_ny = folium.Map(location=[latitude, longitude], zoom_start=12)


for lat, lng, label in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Neighborhood']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_hk)  
    
map_ny

In [186]:
#Using foursquare 
CLIENT_ID = 'I3VJK12ON5FSPNQZDGWEYZJ4MCEM1CEL2DJJ1BLYM3PRSXIS'
CLIENT_SECRET = 'KPCTUWXQESIT4EPK2PUOIDDJR4NARSIDYSW2M11XVMX3XNQE'
VERSION = '20201005'

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: I3VJK12ON5FSPNQZDGWEYZJ4MCEM1CEL2DJJ1BLYM3PRSXIS
CLIENT_SECRET:KPCTUWXQESIT4EPK2PUOIDDJR4NARSIDYSW2M11XVMX3XNQE


In [187]:
LIMIT = 100
radius = 1000

neighborhood_latitude = 40.7127281
neighborhood_longitude = -74.0060152


url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    neighborhood_latitude, 
    neighborhood_longitude, 
    radius, 
    LIMIT)

url

'https://api.foursquare.com/v2/venues/explore?&client_id=I3VJK12ON5FSPNQZDGWEYZJ4MCEM1CEL2DJJ1BLYM3PRSXIS&client_secret=KPCTUWXQESIT4EPK2PUOIDDJR4NARSIDYSW2M11XVMX3XNQE&v=20201005&ll=40.7127281,-74.0060152&radius=1000&limit=100'

In [188]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5eb7b2ee60ba08001bb8f3ec'},
 'response': {'suggestedFilters': {'header': 'Tap to show:',
   'filters': [{'name': '$-$$$$', 'key': 'price'},
    {'name': 'Open now', 'key': 'openNow'}]},
  'headerLocation': 'Downtown Manhattan',
  'headerFullLocation': 'Downtown Manhattan, New York',
  'headerLocationGranularity': 'neighborhood',
  'totalResults': 234,
  'suggestedBounds': {'ne': {'lat': 40.72172810900001,
    'lng': -73.99416384126839},
   'sw': {'lat': 40.70372809099999, 'lng': -74.0178665587316}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '57f0689d498e7d49d9189369',
       'name': 'The Bar Room at Temple Court',
       'location': {'address': '123 Nassau St',
        'lat': 40.7114477287544,
        'lng': -74.00680157032005,
 

In [189]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    venues_list=[]
    
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [190]:
ny_venues = getNearbyVenues(names=neighborhoods['Neighborhood'],
                                   latitudes=neighborhoods['Latitude'],
                                   longitudes=neighborhoods['Longitude']
                                  )

Wakefield
Co-op City
Eastchester
Fieldston
Riverdale
Kingsbridge
Marble Hill
Woodlawn
Norwood
Williamsbridge
Baychester
Pelham Parkway
City Island
Bedford Park
University Heights
Morris Heights
Fordham
East Tremont
West Farms
High  Bridge
Melrose
Mott Haven
Port Morris
Longwood
Hunts Point
Morrisania
Soundview
Clason Point
Throgs Neck
Country Club
Parkchester
Westchester Square
Van Nest
Morris Park
Belmont
Spuyten Duyvil
North Riverdale
Pelham Bay
Schuylerville
Edgewater Park
Castle Hill
Olinville
Pelham Gardens
Concourse
Unionport
Edenwald
Bay Ridge
Bensonhurst
Sunset Park
Greenpoint
Gravesend
Brighton Beach
Sheepshead Bay
Manhattan Terrace
Flatbush
Crown Heights
East Flatbush
Kensington
Windsor Terrace
Prospect Heights
Brownsville
Williamsburg
Bushwick
Bedford Stuyvesant
Brooklyn Heights
Cobble Hill
Carroll Gardens
Red Hook
Gowanus
Fort Greene
Park Slope
Cypress Hills
East New York
Starrett City
Canarsie
Flatlands
Mill Island
Manhattan Beach
Coney Island
Bath Beach
Borough Park
Dyker

In [191]:
print(ny_venues.shape)
ny_venues.head()

(9826, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0    Wakefield              40.894705              -73.847201   
1    Wakefield              40.894705              -73.847201   
2    Wakefield              40.894705              -73.847201   
3    Wakefield              40.894705              -73.847201   
4    Wakefield              40.894705              -73.847201   

              Venue  Venue Latitude  Venue Longitude  Venue Category  
0  Lollipops Gelato       40.894123       -73.845892    Dessert Shop  
1  Carvel Ice Cream       40.890487       -73.848568  Ice Cream Shop  
2         Walgreens       40.896528       -73.844700        Pharmacy  
3          Rite Aid       40.896649       -73.844846        Pharmacy  
4           Dunkin'       40.890459       -73.849089      Donut Shop

In [192]:
ny_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  \
Neighborhood                                                               
Allerton                                      32                      32   
Annadale                                      12                      12   
Arden Heights                                  4                       4   
Arlington                                      5                       5   
Arrochar                                      20                      20   
Arverne                                       18                      18   
Astoria                                       98                      98   
Astoria Heights                               13                      13   
Auburndale                                    18                      18   
Bath Beach                                    42                      42   
Battery Park City                             60                      60   
Bay Ridge                                     82                      82   
Bay Terrace                                   47                      47   
Baychester                                    22                      22   
Bayside                                       73                      73   
Bayswater                                      2                       2   
Bedford Park                                  36                      36   
Bedford Stuyvesant                            27                      27   
Beechhurst                                    15                      15   
Bellaire                                      13                      13   
Belle Harbor                                  17                      17   
Bellerose                                     19                      19   
Belmont                                      100                     100   
Bensonhurst                                   26                      26   
Bergen Beach                                   7                       7   
Blissville                                    17                      17   
Bloomfield                                     5                       5   
Boerum Hill                                   92                      92   
Borough Park                                  18                      18   
Breezy Point                                   3                       3   
Briarwood                                     11                      11   
Brighton Beach                                44                      44   
Broad Channel                                  6                       6   
Broadway Junction                             16                      16   
Bronxdale                                     12                      12   
Brooklyn Heights                             100                     100   
Brookville                                     1                       1   
Brownsville                                   16                      16   
Bulls Head                                    44                      44   
Bushwick                                      74                      74   
Butler Manor                                   5                       5   
Cambria Heights                               14                      14   
Canarsie                                       7                       7   
Carnegie Hill                                 86                      86   
Carroll Gardens                              100                     100   
Castle Hill                                    7                       7   
Castleton Corners                             16                      16   
Central Harlem                                45                      45   
Charleston                                    29                      29   
Chelsea                                      107                     107   
Chinatown                                    100                     100   

In [193]:
print('There are {} uniques categories.'.format(len(ny_venues['Venue Category'].unique())))

There are 427 uniques categories.


In [194]:
#using onehot encoding
ny_onehot = pd.get_dummies(ny_venues[['Venue Category']], prefix="", prefix_sep="")

ny_onehot['Neighborhood'] = ny_venues['Neighborhood'] 


fixed_columns = [ny_onehot.columns[-1]] + list(ny_onehot.columns[:-1])
ny_onehot = ny_onehot[fixed_columns]

ny_onehot.head()

Yoga Studio  Accessories Store  Adult Boutique  Afghan Restaurant  \
0            0                  0               0                  0   
1            0                  0               0                  0   
2            0                  0               0                  0   
3            0                  0               0                  0   
4            0                  0               0                  0   

   African Restaurant  American Restaurant  Animal Shelter  Antique Shop  \
0                   0                    0               0             0   
1                   0                    0               0             0   
2                   0                    0               0             0   
3                   0                    0               0             0   
4                   0                    0               0             0   

   Arcade  Arepa Restaurant  Argentinian Restaurant  Art Gallery  Art Museum  \
0       0                 0                       0            0           0   
1       0                 0                       0            0           0   
2       0                 0                       0            0           0   
3       0                 0                       0            0           0   
4       0                 0                       0            0           0   

   Arts & Crafts Store  Arts & Entertainment  Asian Restaurant  Astrologer  \
0                    0                     0                 0           0   
1                    0                     0                 0           0   
2                    0                     0                 0           0   
3                    0                     0                 0           0   
4                    0                     0                 0           0   

   Athletics & Sports  Auditorium  Australian Restaurant  Austrian Restaurant  \
0                   0           0                      0                    0   
1                   0           0                      0                    0   
2                   0           0                      0                    0   
3                   0           0                      0                    0   
4                   0           0                      0                    0   

   Auto Garage  Automotive Shop  BBQ Joint  Baby Store  Bagel Shop  Bakery  \
0            0                0          0           0           0       0   
1            0                0          0           0           0       0   
2            0                0          0           0           0       0   
3            0                0          0           0           0       0   
4            0                0          0           0           0       0   

   Bank  Bar  Baseball Field  Baseball Stadium  Basketball Court  \
0     0    0               0                 0                 0   
1     0    0               0                 0                 0   
2     0    0               0                 0                 0   
3     0    0               0                 0                 0   
4     0    0               0                 0                 0   

   Basketball Stadium  Bath House  Beach  Beach Bar  Bed & Breakfast  \
0                   0           0      0          0                0   
1                   0           0      0          0                0   
2                   0           0      0          0                0   
3                   0           0      0          0                0   
4                   0           0      0          0                0   

   Beer Bar  Beer Garden  Beer Store  Big Box Store  Bike Rental / Bike Share  \
0         0            0           0              0                         0   
1         0            0           0              0                         0   
2         0            0           0              0                         0   
3         0            0           0     

In [195]:
ny_onehot.shape

(9826, 427)

In [196]:
ny_grouped = ny_onehot.groupby('Neighborhood').mean().reset_index()
ny_grouped

Neighborhood  Yoga Studio  Accessories Store  \
0                     Allerton     0.000000           0.000000   
1                     Annadale     0.000000           0.000000   
2                Arden Heights     0.000000           0.000000   
3                    Arlington     0.000000           0.000000   
4                     Arrochar     0.000000           0.000000   
5                      Arverne     0.000000           0.000000   
6                      Astoria     0.000000           0.000000   
7              Astoria Heights     0.000000           0.000000   
8                   Auburndale     0.000000           0.000000   
9                   Bath Beach     0.000000           0.000000   
10           Battery Park City     0.000000           0.000000   
11                   Bay Ridge     0.000000           0.000000   
12                 Bay Terrace     0.000000           0.021277   
13                  Baychester     0.000000           0.000000   
14                     Bayside     0.013699           0.000000   
15                   Bayswater     0.000000           0.000000   
16                Bedford Park     0.000000           0.000000   
17          Bedford Stuyvesant     0.000000           0.000000   
18                  Beechhurst     0.066667           0.000000   
19                    Bellaire     0.000000           0.000000   
20                Belle Harbor     0.000000           0.000000   
21                   Bellerose     0.000000           0.000000   
22                     Belmont     0.000000           0.000000   
23                 Bensonhurst     0.000000           0.000000   
24                Bergen Beach     0.000000           0.000000   
25                  Blissville     0.000000           0.000000   
26                  Bloomfield     0.000000           0.000000   
27                 Boerum Hill     0.021739           0.000000   
28                Borough Park     0.000000           0.000000   
29                Breezy Point     0.000000           0.000000   
30                   Briarwood     0.000000           0.000000   
31              Brighton Beach     0.000000           0.000000   
32               Broad Channel     0.000000           0.000000   
33           Broadway Junction     0.000000           0.000000   
34                   Bronxdale     0.000000           0.000000   
35            Brooklyn Heights     0.040000           0.000000   
36                  Brookville     0.000000           0.000000   
37                 Brownsville     0.000000           0.000000   
38                  Bulls Head     0.000000           0.000000   
39                    Bushwick     0.000000           0.000000   
40                Butler Manor     0.000000           0.000000   
41             Cambria Heights     0.000000           0.000000   
42                    Canarsie     0.000000           0.000000   
43               Carnegie Hill     0.034884           0.000000   
44             Carroll Gardens     0.000000           0.000000   
45                 Castle Hill     0.000000           0.000000   
46           Castleton Corners     0.000000           0.000000   
47              Central Harlem     0.000000           0.000000   
48                  Charleston     0.000000           0.000000   
49                     Chelsea     0.000000           0.000000   
50                   Chinatown     0.010000           0.000000   
51                 City Island     0.000000           0.000000   
52                   City Line     0.000000           0.000000   
53                Civic Center     0.034091           0.000000   
54           Claremont Village     0.000000           0.000000   
55                Clason Point     0.000000           0.000000   
56                     Clifton     0.000000           0.000000   
57                     Clinton     0.000000           0.000000   
58                Clinton Hill     0.031250           0.000000   
59                  Co-op City     0.000000           0.00

In [197]:
ny_grouped.shape

(300, 427)

In [198]:
missing_neighborhood = [i for i in neighborhoods['Neighborhood'].unique() if i not in neighborhoods['Neighborhood'].unique()]

missing_neighborhood

[]

In [199]:
num_top_venues = 5

for hood in ny_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = ny_grouped[ny_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Allerton----
                venue  freq
0         Pizza Place  0.16
1       Deli / Bodega  0.06
2  Chinese Restaurant  0.06
3         Supermarket  0.06
4        Intersection  0.03


----Annadale----
                 venue  freq
0  American Restaurant  0.17
1                Diner  0.08
2                  Pub  0.08
3        Deli / Bodega  0.08
4        Train Station  0.08


----Arden Heights----
                  venue  freq
0              Pharmacy  0.25
1           Pizza Place  0.25
2           Coffee Shop  0.25
3              Bus Stop  0.25
4  Pakistani Restaurant  0.00


----Arlington----
                 venue  freq
0        Grocery Store   0.2
1        Deli / Bodega   0.2
2  American Restaurant   0.2
3        Boat or Ferry   0.2
4             Bus Stop   0.2


----Arrochar----
                   venue  freq
0            Pizza Place  0.10
1          Deli / Bodega  0.10
2     Italian Restaurant  0.10
3               Bus Stop  0.10
4  Outdoors & Recreation  0.05


----Arverne----
 

In [200]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [229]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = ny_grouped['Neighborhood']

for ind in np.arange(ny_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(ny_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0       Allerton           Pizza Place         Deli / Bodega   
1       Annadale   American Restaurant                  Park   
2  Arden Heights              Pharmacy           Coffee Shop   
3      Arlington         Deli / Bodega   American Restaurant   
4       Arrochar           Pizza Place              Bus Stop   

  3rd Most Common Venue 4th Most Common Venue  5th Most Common Venue  \
0    Chinese Restaurant           Supermarket  Check Cashing Service   
1         Deli / Bodega           Pizza Place                  Diner   
2           Pizza Place              Bus Stop          Women's Store   
3         Boat or Ferry         Grocery Store               Bus Stop   
4    Italian Restaurant         Deli / Bodega      Polish Restaurant   

  6th Most Common Venue       7th Most Common Venue  \
0                Bakery           Electronics Store   
1              Pharmacy               Train Station   
2  Fast Food Restaurant        Ethiopian Restaurant   
3         Women's Store  Financial or Legal Service   
4           Supermarket          Athletics & Sports   

       8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
0          Martial Arts Dojo           Gas Station               Pharmacy  
1                 Restaurant            Sports Bar                    Pub  
2              Event Service           Event Space                Exhibit  
3                Event Space               Exhibit                Factory  
4  Middle Eastern Restaurant        Sandwich Place                  Hotel

In [230]:

# set number of clusters
kclusters = 5

ny_grouped_clustering = ny_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(ny_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([4, 4, 2, 2, 1, 4, 4, 4, 4, 4], dtype=int32)

In [231]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

ny_merged = neighborhoods
ny_merged = ny_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')
ny_merged.head() # check the last columns!

Borough Neighborhood   Latitude  Longitude  Cluster Labels  \
0   Bronx    Wakefield  40.894705 -73.847201             4.0   
1   Bronx   Co-op City  40.874294 -73.829939             4.0   
2   Bronx  Eastchester  40.887556 -73.827806             1.0   
3   Bronx    Fieldston  40.895437 -73.905643             4.0   
4   Bronx    Riverdale  40.890834 -73.912585             4.0   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0              Pharmacy            Laundromat        Sandwich Place   
1  Fast Food Restaurant           Bus Station           Pizza Place   
2           Bus Station  Caribbean Restaurant         Deli / Bodega   
3                 Plaza      Business Service                 River   
4           Bus Station                  Park                  Bank   

  4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0            Donut Shop           Gas Station          Dessert Shop   
1        Mattress Store          Liquor Store        Discount Store   
2                 Diner              Bus Stop            Donut Shop   
3           Bus Station  Ethiopian Restaurant         Event Service   
4                 Plaza                   Gym        Baseball Field   

  7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
0        Ice Cream Shop                  Food               Exhibit   
1         Grocery Store            Bagel Shop            Restaurant   
2         Metro Station    Seafood Restaurant       Automotive Shop   
3           Event Space               Exhibit               Factory   
4          Home Service            Playground            Food Truck   

  10th Most Common Venue  
0            Event Space  
1         Ice Cream Shop  
2   Fast Food Restaurant  
3     Falafel Restaurant  
4                  Diner

In [242]:
ny_merged1=ny_merged.dropna(how='all')

In [245]:
ny_merged1.isnull()

Borough  Neighborhood  Latitude  Longitude  Cluster Labels  \
0      False         False     False      False           False   
1      False         False     False      False           False   
2      False         False     False      False           False   
3      False         False     False      False           False   
4      False         False     False      False           False   
5      False         False     False      False           False   
6      False         False     False      False           False   
7      False         False     False      False           False   
8      False         False     False      False           False   
9      False         False     False      False           False   
10     False         False     False      False           False   
11     False         False     False      False           False   
12     False         False     False      False           False   
13     False         False     False      False           False   
14     False         False     False      False           False   
15     False         False     False      False           False   
16     False         False     False      False           False   
17     False         False     False      False           False   
18     False         False     False      False           False   
19     False         False     False      False           False   
20     False         False     False      False           False   
21     False         False     False      False           False   
22     False         False     False      False           False   
23     False         False     False      False           False   
24     False         False     False      False           False   
25     False         False     False      False           False   
26     False         False     False      False           False   
27     False         False     False      False           False   
28     False         False     False      False           False   
29     False         False     False      False           False   
30     False         False     False      False           False   
31     False         False     False      False           False   
32     False         False     False      False           False   
33     False         False     False      False           False   
34     False         False     False      False           False   
35     False         False     False      False           False   
36     False         False     False      False           False   
37     False         False     False      False           False   
38     False         False     False      False           False   
39     False         False     False      False           False   
40     False         False     False      False           False   
41     False         False     False      False           False   
42     False         False     False      False           False   
43     False         False     False      False           False   
44     False         False     False      False           False   
45     False         False     False      False           False   
46     False         False     False      False           False   
47     False         False     False      False           False   
48     False         False     False      False           False   
49     False         False     False      False           False   
50     False         False     False      False           False   
51     False         False     False      False           False   
52     False         False     False      False           False   
53     False         False     False      False           False   
54     False         False     False      False           False   
55     False         False     False      False           False   
56     False         False     False      False           False   
57     False         False     False      False           False   
58     False         False     False      False     

In [268]:
ny_merged['Cluster Labels']=ny_merged['Cluster Labels'].astype('int64')



In [281]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=12)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(ny_merged1['Latitude'], ny_merged1['Longitude'], ny_merged1['Neighborhood'], ny_merged1['Cluster Labels']):
    label = folium.Popup(str(poi) + ' cluster ' + str(cluster+1), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        fill=True,
       
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [275]:
#cluster1
ny_merged.loc[ny_merged['Cluster Labels'] == 0, ny_merged.columns[[1] + list(range(5, ny_merged.shape[1]))]]

Neighborhood 1st Most Common Venue      2nd Most Common Venue  \
27   Clason Point                  Park  South American Restaurant   
192    Somerville                  Park              Women's Store   
203     Todt Hill                  Park              Women's Store   
255  Emerson Hill                     0                          0   
257  Howland Hook                     0                          0   
303     Bayswater                  Park                 Playground   

    3rd Most Common Venue 4th Most Common Venue  5th Most Common Venue  \
27          Boat or Ferry         Grocery Store                   Pool   
192    English Restaurant  Ethiopian Restaurant          Event Service   
203    English Restaurant  Ethiopian Restaurant          Event Service   
255                     0                     0                      0   
257                     0                     0                      0   
303         Women's Store  Fast Food Restaurant  Entertainment Service   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
27               Bus Stop         Women's Store         Event Service   
192           Event Space               Exhibit               Factory   
203           Event Space               Exhibit               Factory   
255                     0                     0                     0   
257                     0                     0                     0   
303  Ethiopian Restaurant         Event Service           Event Space   

    9th Most Common Venue 10th Most Common Venue  
27            Event Space                Exhibit  
192    Falafel Restaurant                   Farm  
203    Falafel Restaurant                   Farm  
255                     0                      0  
257                     0                      0  
303               Exhibit                Factory

In [276]:
#cluster2
ny_merged.loc[ny_merged['Cluster Labels'] == 1, ny_merged.columns[[1] + list(range(5, ny_merged.shape[1]))]]



Neighborhood 1st Most Common Venue            2nd Most Common Venue  \
2          Eastchester           Bus Station             Caribbean Restaurant   
7             Woodlawn         Deli / Bodega                       Playground   
28         Throgs Neck         Deli / Bodega                      Coffee Shop   
32            Van Nest           Pizza Place                    Deli / Bodega   
39      Edgewater Park    Italian Restaurant                    Deli / Bodega   
72       East New York         Deli / Bodega               Spanish Restaurant   
83         Marine Park           Pizza Place               Chinese Restaurant   
89          Ocean Hill         Deli / Bodega  Southern / Soul Food Restaurant   
148   South Ozone Park         Deli / Bodega                             Park   
150         Whitestone          Dance Studio                    Deli / Bodega   
171      Broad Channel              Dive Bar                    Deli / Bodega   
190       Belle Harbor                 Beach                              Spa   
193         Brookville         Deli / Bodega                    Women's Store   
195       North Corona         Deli / Bodega                      Pizza Place   
204        South Beach                  Pier                    Deli / Bodega   
205      Port Richmond   Rental Car Location                 Basketball Court   
206   Mariner's Harbor    Italian Restaurant                    Deli / Bodega   
210             Travis                 Hotel                    Deli / Bodega   
217        Tottenville              Bus Stop               Italian Restaurant   
222            Wingate   Fried Chicken Joint                    Deli / Bodega   
228           Arrochar           Pizza Place                         Bus Stop   
232      Midland Beach                 Beach                Electronics Store   
234     New Dorp Beach    Italian Restaurant                    Deli / Bodega   
252        Shore Acres    Italian Restaurant                         Bus Stop   
254            Concord         Deli / Bodega               Chinese Restaurant   
264             Utopia         Deli / Bodega                      Pizza Place   
267  Claremont Village           Bus Station                    Deli / Bodega   
278         Blissville           Bus Station                    Deli / Bodega   
284      Manor Heights          Liquor Store                    Deli / Bodega   
288            Roxbury        Baseball Field                        Irish Pub   
295      Highland Park         Deli / Bodega                    Metro Station   
296            Madison            Bagel Shop               Italian Restaurant   

          3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
2                 Deli / Bodega                 Diner              Bus Stop   
7                           Pub           Pizza Place     Food & Drink Shop   
28           Italian Restaurant             Juice Bar                   Bar   
32                   Hookah Bar            Donut Shop           Coffee Shop   
39                  Coffee Shop           Pizza Place                   Bar   
72         Caribbean Restaurant         Event Service   Fried Chicken Joint   
83               Baseball Field                   Gym           Coffee Shop   
89           Chinese Restaurant   Fried Chicken Joint     Convenience Store   
148                         Bar  Fast Food Restaurant        Sandwich Place   
150             Bubble Tea Shop           Candy Store         Historic Site   
171         Sporting Goods Shop       Other Nightlife           Bus Station   
190                         Pub         Deli / Bodega    Italian Restaurant   
193  Financial or Legal Service  Ethiopian Restaurant         Event Service   
195                       Hotel                Bakery  Gym / Fitness Center   
204                       Beach              Bus Stop    Athletics & Sports   
205               Deli / Bodega            Donut Shop              Bus S

In [277]:
#cluster3
ny_merged.loc[ny_merged['Cluster Labels'] == 2, ny_merged.columns[[1] + list(range(5, ny_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
77   Manhattan Beach                  Café              Bus Stop   
198     New Brighton              Bus Stop         Deli / Bodega   
202      Grymes Hill               Dog Run              Bus Stop   
224        Park Hill              Bus Stop    Athletics & Sports   
226     Graniteville         Boat or Ferry         Grocery Store   
227        Arlington         Deli / Bodega   American Restaurant   
241    Arden Heights              Pharmacy           Coffee Shop   
245       Bloomfield     Recreation Center        Discount Store   
256    Randall Manor              Bus Stop            Playground   
258         Elm Park              Bus Stop    Italian Restaurant   
285      Willowbrook              Bus Stop    Chinese Restaurant   
305        Fox Hills              Bus Stop             BBQ Joint   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
77                  Beach            Playground        Sandwich Place   
198                  Park         Bowling Alley        Discount Store   
202         Women's Store   Filipino Restaurant  Ethiopian Restaurant   
224                 Hotel  Gym / Fitness Center           Coffee Shop   
226              Bus Stop        Sandwich Place         Women's Store   
227         Boat or Ferry         Grocery Store              Bus Stop   
241           Pizza Place              Bus Stop         Women's Store   
245            Theme Park                  Park              Bus Stop   
256            Bagel Shop                  Park         Women's Store   
258   American Restaurant        Ice Cream Shop       Laundry Service   
285            Bagel Shop           Pizza Place         Women's Store   
305         Grocery Store        Sandwich Place         Women's Store   

    6th Most Common Venue       7th Most Common Venue 8th Most Common Venue  \
77            Pizza Place              Ice Cream Shop                  Food   
198            Playground  Financial or Legal Service           Event Space   
202         Event Service                 Event Space               Exhibit   
224         Women's Store        Ethiopian Restaurant         Event Service   
226                 Field        Ethiopian Restaurant         Event Service   
227         Women's Store  Financial or Legal Service           Event Space   
241  Fast Food Restaurant        Ethiopian Restaurant         Event Service   
245     Food & Drink Shop              Farmers Market  Ethiopian Restaurant   
256  Ethiopian Restaurant               Event Service           Event Space   
258            Toll Plaza                 Pizza Place         Deli / Bodega   
285  Fast Food Restaurant       Entertainment Service  Ethiopian Restaurant   
305  Fast Food Restaurant        Ethiopian Restaurant         Event Service   

    9th Most Common Venue 10th Most Common Venue  
77                Exhibit            Event Space  
198               Exhibit                Factory  
202               Factory     Falafel Restaurant  
224           Event Space                Exhibit  
226           Event Space                Exhibit  
227               Exhibit                Factory  
241           Event Space                Exhibit  
245            Food Truck          Event Service  
256               Exhibit                Factory  
258           Event Space                Factory  
285         Event Service            Event Space  
305           Event Space                Exhibit

In [278]:
#cluster4
ny_merged.loc[ny_merged['Cluster Labels'] == 3, ny_merged.columns[[1] + list(range(5, ny_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
76  Mill Island                  Pool         Women's Store   

   3rd Most Common Venue  4th Most Common Venue 5th Most Common Venue  \
76   Filipino Restaurant  Entertainment Service  Ethiopian Restaurant   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
76         Event Service           Event Space               Exhibit   

   9th Most Common Venue 10th Most Common Venue  
76               Factory     Falafel Restaurant

In [279]:
#cluster5
ny_merged.loc[ny_merged['Cluster Labels'] == 4, ny_merged.columns[[1] + list(range(5, ny_merged.shape[1]))]]

Neighborhood            1st Most Common Venue  \
0                    Wakefield                         Pharmacy   
1                   Co-op City             Fast Food Restaurant   
3                    Fieldston                            Plaza   
4                    Riverdale                      Bus Station   
5                  Kingsbridge                      Pizza Place   
6                  Marble Hill                   Sandwich Place   
8                      Norwood                      Pizza Place   
9               Williamsbridge                        Nightclub   
10                  Baychester                       Donut Shop   
11              Pelham Parkway                      Pizza Place   
12                 City Island                  Harbor / Marina   
13                Bedford Park                            Diner   
14          University Heights                      Pizza Place   
15              Morris Heights               Chinese Restaurant   
16                     Fordham                Mobile Phone Shop   
17                East Tremont                      Pizza Place   
18                  West Farms                      Bus Station   
19                High  Bridge                         Pharmacy   
20                     Melrose                      Pizza Place   
21                  Mott Haven                              Gym   
22                 Port Morris           Furniture / Home Store   
23                    Longwood             Fast Food Restaurant   
24                 Hunts Point                             Bank   
25                  Morrisania                      Bus Station   
26                   Soundview               Chinese Restaurant   
29                Country Club                   Sandwich Place   
30                 Parkchester                      Supermarket   
31          Westchester Square             Fast Food Restaurant   
33                 Morris Park                      Pizza Place   
34                     Belmont               Italian Restaurant   
35              Spuyten Duyvil                             Park   
36             North Riverdale                      Pizza Place   
37                  Pelham Bay               Italian Restaurant   
38               Schuylerville                             Bank   
40                 Castle Hill                           Market   
41                   Olinville             Caribbean Restaurant   
42              Pelham Gardens                       Donut Shop   
43                   Concourse                    Grocery Store   
44                   Unionport                       Donut Shop   
45                    Edenwald                      Supermarket   
46                   Bay Ridge                              Spa   
47                 Bensonhurst               Italian Restaurant   
48                 Sunset Park                           Bakery   
49                  Greenpoint                              Bar   
50                   Gravesend               Chinese Restaurant   
51              Brighton Beach               Russian Restaurant   
52              Sheepshead Bay               Turkish Restaurant   
53           Manhattan Terrace                      Pizza Place   
54                    Flatbush                    Deli / Bodega   
55               Crown Heights                      Pizza Place   
56               East Flatbush               Chinese Restaurant   
57                  Kensington                  Thai Restaurant   
58             Windsor Terrace                    Deli / Bodega   
59            Prospect Heights                              Bar   
60                 Brownsville                       Restaurant   
61                Williamsburg                      Coffee Shop   
62                    Bushwick                              Bar   
63          Bedford Stuyvesant                      Pizza Place   
64            Brooklyn Heights                      Yoga Studio  

<b>Conclusion</b>
Our problem is
"Where is the proper location in NewYork to open a restaurant". We dont consider the clusters 1,3 and 4 because they are not good places to open a restaurant as it wont be a profitable business

After examining cluster 2 and cluster 5, We can say that these are most profitable places as these as parks and other restaurants which can help the hotel business. There are many bus stops and public transport available for easy reachout to the hotel. This helps to the place being more useful.

So we can say that clusters 2 and 5 are very good places to open a restaurant in NewYork.